In [1]:
from __windmodel3x3DAC__ import glob_all, save_models, WindLossmodel, define_composite_wind_model
from __windmodel3x3DAC__ import define_generator, define_discriminator, define_composite_model, train
from tensorflow.keras import backend as K

import warnings
warnings.filterwarnings('ignore')
import logging
logging.getLogger().disabled = True

import pandas as pd
import numpy as np
import tensorflow.compat.v1 as tf
import os

os.environ["CUDA_VISIBLE_DEVICES"] = "0"
tf.config.optimizer.set_jit(True)

In [2]:
resnet_n = 9 ; epochs = 500; batch = 1

home = '/media/disk3/weisting/CycleGan/Experiment5/'

dataA_norm = np.load('new_dataA_norm.npy')
dataB_norm = np.load('new_dataB_norm.npy')
print('Loaded', dataA_norm.shape, dataB_norm.shape)

EPA73_testing_PM25 = np.load(home+'348X204/EPA73_Testing_348X204_PM25.npy', mmap_mode='r')[:3000]


Train_Direc = np.concatenate([np.load('CWBEPA_Content_WIND_DIREC_graph_Training_K3.npy'),
                             np.load('CWBEPA_Content_WIND_DIREC_graph_Training_K3.npy')])

Train_Speed = np.concatenate([np.load('CWBEPA_Content_WIND_SPEED_graph_Training_K3.npy'),
                             np.load('CWBEPA_Content_WIND_SPEED_graph_Training_K3.npy')])

station_coordinate = pd.read_csv('RandomTesting/station_coordinate')
extract5_list = np.load('RandomTesting/extract5_list.npy')
extract10_list = np.load('RandomTesting/extract10_list.npy')
extract15_list = np.load('RandomTesting/extract15_list.npy')
extract20_list = np.load('RandomTesting/extract20_list.npy')

ex20_KNNhalf = np.load('ex20_KNN_half.npy', mmap_mode='r')
ex20_KNN_norm = np.load('ex20_KNN_norm.npy', mmap_mode='r')[:,:3000,:,:]

model_path = 'CWBEPA_Graph_RMSprop_Res'+str(resnet_n)+'_CycleGan_3x3DAwind/'
if not os.path.exists(model_path+'result/'):os.makedirs(model_path+'result/')

Loaded (3194, 348, 204, 1) (3194, 348, 204, 1)


In [ ]:
K.clear_session()
image_shape = dataB_norm[0].shape
g_model_AtoB = define_generator(image_shape,resnet_n)
print('generator: A -> B')
g_model_BtoA = define_generator(image_shape,resnet_n)
print('generator: B -> A')
d_model_A = define_discriminator(image_shape, d_lr=5e-5)
print('discriminator: A -> [real/fake]')
d_model_B = define_discriminator(image_shape, d_lr=5e-5)
print('discriminator: B -> [real/fake]')
c_model_AtoB = define_composite_model(g_model_AtoB, d_model_B, g_model_BtoA, image_shape, g_lr = 1e-3)
print('composite: A -> B -> [real/fake, A]')
c_model_BtoA = define_composite_model(g_model_BtoA, d_model_A, g_model_AtoB, image_shape, g_lr = 1e-3)
print('composite: B -> A -> [real/fake, B]')

WindLoss_model = WindLossmodel()
print('WindLoss_model')
c_model_wind = define_composite_wind_model(g_model_AtoB, WindLoss_model, image_shape, g_lr= 1e-5)
print('composite_wind_model')

train(d_model_A, d_model_B, g_model_AtoB, g_model_BtoA, c_model_AtoB, c_model_BtoA, c_model_wind,
      dataA_norm, dataB_norm, model_path, EPA73_testing_PM25, Train_Direc, Train_Speed,
      station_coordinate, extract5_list, extract10_list, extract15_list, extract20_list, ex20_KNN_norm, 
      ex20_KNNhalf, n_epochs=epochs, n_batch=batch, save_epochs = 1)

print('train models done')

generator: A -> B
generator: B -> A
discriminator: A -> [real/fake]
discriminator: B -> [real/fake]
composite: A -> B -> [real/fake, A]
composite: B -> A -> [real/fake, B]
WindLoss_model
composite_wind_model
3194
>00001, dALoss[1.260,1.251] dAAcc[0.353,0.562] dBLoss[0.754,0.975] dBAcc[0.171,0.474] g[20.312,22.794] wind[0.338]
>00002, dALoss[6.218,7.079] dAAcc[0.444,0.666] dBLoss[5.584,2.200] dBAcc[0.570,0.701] g[25.692,20.953] wind[0.212]
>00003, dALoss[2.422,4.848] dAAcc[0.461,0.237] dBLoss[7.575,1.191] dBAcc[0.660,0.563] g[31.926,34.629] wind[0.130]
>00004, dALoss[2.532,1.438] dAAcc[0.487,0.689] dBLoss[1.787,1.175] dBAcc[0.430,0.570] g[22.349,26.052] wind[0.169]
>00005, dALoss[0.788,1.013] dAAcc[0.473,0.334] dBLoss[0.316,2.627] dBAcc[0.666,0.570] g[24.527,22.270] wind[0.130]
>00006, dALoss[0.911,0.668] dAAcc[0.462,0.800] dBLoss[0.411,3.317] dBAcc[0.466,0.408] g[24.055,21.295] wind[0.295]
>00007, dALoss[0.921,0.903] dAAcc[0.608,0.388] dBLoss[0.226,1.218] dBAcc[0.549,0.636] g[17.982,18

>00071, dALoss[0.195,0.089] dAAcc[0.841,0.870] dBLoss[0.186,0.034] dBAcc[0.833,0.957] g[14.393,14.323] wind[0.158]
>00072, dALoss[0.354,0.207] dAAcc[0.557,0.881] dBLoss[0.120,0.170] dBAcc[0.940,0.691] g[14.559,13.832] wind[0.192]
>00073, dALoss[0.162,0.127] dAAcc[0.863,0.925] dBLoss[0.106,0.111] dBAcc[0.893,0.927] g[16.900,16.617] wind[0.316]
>00074, dALoss[0.455,0.153] dAAcc[0.695,0.753] dBLoss[0.157,0.045] dBAcc[0.891,0.969] g[14.644,14.497] wind[0.153]
>00075, dALoss[0.248,0.134] dAAcc[0.769,0.994] dBLoss[0.130,0.065] dBAcc[0.781,0.944] g[14.436,14.750] wind[0.312]
>00076, dALoss[0.168,0.031] dAAcc[0.892,0.934] dBLoss[0.085,0.070] dBAcc[0.896,0.838] g[15.649,15.688] wind[0.262]
>00077, dALoss[0.221,0.045] dAAcc[0.570,0.973] dBLoss[0.091,0.064] dBAcc[0.888,0.975] g[12.311,11.263] wind[0.216]
>00078, dALoss[0.098,0.046] dAAcc[0.905,0.883] dBLoss[0.102,0.039] dBAcc[0.809,0.924] g[14.795,15.175] wind[0.333]
>00079, dALoss[0.112,0.039] dAAcc[0.798,1.000] dBLoss[0.161,0.042] dBAcc[0.862,0

>00143, dALoss[0.070,0.010] dAAcc[0.904,0.999] dBLoss[0.065,0.027] dBAcc[0.917,0.958] g[12.895,13.385] wind[0.157]
>00144, dALoss[0.073,0.058] dAAcc[0.811,0.879] dBLoss[0.050,0.006] dBAcc[0.956,0.993] g[13.635,12.153] wind[0.460]
>00145, dALoss[0.069,0.070] dAAcc[0.989,0.998] dBLoss[0.057,0.033] dBAcc[0.944,0.999] g[11.981,11.991] wind[0.113]
>00146, dALoss[0.127,0.074] dAAcc[0.938,0.886] dBLoss[0.064,0.068] dBAcc[0.921,0.887] g[13.171,13.897] wind[0.233]
>00147, dALoss[0.083,0.034] dAAcc[0.931,0.999] dBLoss[0.063,0.020] dBAcc[0.868,1.000] g[13.003,12.055] wind[0.247]
>00148, dALoss[0.020,0.009] dAAcc[0.992,0.994] dBLoss[0.034,0.008] dBAcc[0.957,0.996] g[12.024,12.100] wind[0.273]
>00149, dALoss[0.077,0.050] dAAcc[0.872,0.895] dBLoss[0.059,0.011] dBAcc[0.985,0.997] g[13.863,13.344] wind[0.203]
>00150, dALoss[0.102,0.089] dAAcc[0.877,1.000] dBLoss[0.046,0.027] dBAcc[0.890,0.931] g[13.181,12.912] wind[0.161]
>00151, dALoss[0.053,0.046] dAAcc[0.950,0.901] dBLoss[0.039,0.016] dBAcc[0.950,0

>00215, dALoss[0.065,0.009] dAAcc[0.878,0.985] dBLoss[0.110,0.025] dBAcc[0.835,0.910] g[12.390,13.108] wind[0.122]
>00216, dALoss[0.050,0.011] dAAcc[0.930,0.991] dBLoss[0.041,0.004] dBAcc[0.926,0.996] g[12.048,12.132] wind[0.200]
>00217, dALoss[0.043,0.004] dAAcc[0.952,1.000] dBLoss[0.035,0.003] dBAcc[0.959,1.000] g[13.108,13.441] wind[0.206]
>00218, dALoss[0.079,0.007] dAAcc[0.886,1.000] dBLoss[0.034,0.018] dBAcc[0.942,1.000] g[11.596,11.567] wind[0.219]
>00219, dALoss[0.029,0.006] dAAcc[0.944,0.999] dBLoss[0.008,0.023] dBAcc[1.000,0.939] g[10.553,9.999] wind[0.181]
>00220, dALoss[0.038,0.007] dAAcc[1.000,1.000] dBLoss[0.012,0.003] dBAcc[0.996,1.000] g[11.945,12.155] wind[0.240]
>00221, dALoss[0.055,0.006] dAAcc[0.912,1.000] dBLoss[0.018,0.025] dBAcc[0.989,1.000] g[9.663,8.740] wind[0.244]
>00222, dALoss[0.040,0.009] dAAcc[0.971,1.000] dBLoss[0.022,0.002] dBAcc[0.995,1.000] g[12.942,12.541] wind[0.270]
>00223, dALoss[0.023,0.027] dAAcc[0.996,1.000] dBLoss[0.071,0.045] dBAcc[0.861,0.93

>00287, dALoss[0.031,0.023] dAAcc[0.975,0.965] dBLoss[0.019,0.007] dBAcc[0.987,1.000] g[11.142,11.122] wind[0.158]
>00288, dALoss[0.015,0.012] dAAcc[1.000,1.000] dBLoss[0.069,0.073] dBAcc[0.991,1.000] g[11.469,10.857] wind[0.291]
>00289, dALoss[0.030,0.010] dAAcc[1.000,1.000] dBLoss[0.015,0.010] dBAcc[0.978,0.983] g[12.321,12.128] wind[0.232]
>00290, dALoss[0.034,0.034] dAAcc[0.913,0.937] dBLoss[0.027,0.007] dBAcc[0.942,0.982] g[10.771,10.943] wind[0.161]
>00291, dALoss[0.017,0.004] dAAcc[0.992,1.000] dBLoss[0.013,0.008] dBAcc[0.990,1.000] g[10.073,9.864] wind[0.173]
>00292, dALoss[0.053,0.023] dAAcc[0.986,1.000] dBLoss[0.027,0.002] dBAcc[0.994,1.000] g[10.392,10.138] wind[0.245]
>00293, dALoss[0.016,0.024] dAAcc[0.997,0.939] dBLoss[0.030,0.008] dBAcc[0.961,0.991] g[9.655,9.606] wind[0.191]
>00294, dALoss[0.017,0.002] dAAcc[1.000,1.000] dBLoss[0.013,0.013] dBAcc[0.998,0.974] g[9.296,9.181] wind[0.214]
>00295, dALoss[0.029,0.007] dAAcc[0.951,0.998] dBLoss[0.025,0.020] dBAcc[0.997,0.998]

...

>34788, dALoss[0.008,0.009] dAAcc[1.000,1.000] dBLoss[0.070,0.025] dBAcc[0.854,0.984] g[1.869,1.661] wind[0.166]
>34789, dALoss[0.006,0.008] dAAcc[0.996,0.998] dBLoss[0.083,0.038] dBAcc[0.740,0.962] g[1.905,2.172] wind[0.166]
>34790, dALoss[0.005,0.011] dAAcc[0.998,0.994] dBLoss[0.162,0.063] dBAcc[0.465,0.890] g[1.483,1.538] wind[0.207]
>34791, dALoss[0.006,0.014] dAAcc[0.996,1.000] dBLoss[0.033,0.058] dBAcc[1.000,0.861] g[1.182,2.188] wind[0.259]
>34792, dALoss[0.011,0.005] dAAcc[1.000,1.000] dBLoss[0.024,0.033] dBAcc[0.961,0.963] g[1.414,1.598] wind[0.183]
>34793, dALoss[0.020,0.012] dAAcc[1.000,1.000] dBLoss[0.079,0.023] dBAcc[0.834,0.982] g[1.713,1.710] wind[0.154]
>34794, dALoss[0.005,0.003] dAAcc[1.000,1.000] dBLoss[0.010,0.023] dBAcc[0.999,0.994] g[1.283,1.872] wind[0.272]
>34795, dALoss[0.007,0.009] dAAcc[1.000,0.998] dBLoss[0.017,0.012] dBAcc[1.000,0.999] g[1.500,1.802] wind[0.210]
>34796, dALoss[0.003,0.003] dAAcc[1.000,1.000] dBLoss[0.012,0.021] dBAcc[0.988,0.979] g[1.245,1.

>34861, dALoss[0.022,0.007] dAAcc[1.000,1.000] dBLoss[0.136,0.072] dBAcc[0.546,0.853] g[1.569,1.525] wind[0.201]
>34862, dALoss[0.011,0.026] dAAcc[0.993,0.991] dBLoss[0.037,0.045] dBAcc[0.968,0.954] g[1.206,1.349] wind[0.150]
>34863, dALoss[0.003,0.007] dAAcc[1.000,1.000] dBLoss[0.102,0.038] dBAcc[0.705,0.964] g[1.306,1.914] wind[0.100]
>34864, dALoss[0.006,0.006] dAAcc[0.998,0.993] dBLoss[0.053,0.039] dBAcc[1.000,1.000] g[1.670,1.429] wind[0.171]
>34865, dALoss[0.005,0.010] dAAcc[0.993,0.994] dBLoss[0.085,0.078] dBAcc[0.817,0.831] g[1.192,1.695] wind[0.166]
>34866, dALoss[0.004,0.017] dAAcc[0.999,0.994] dBLoss[0.117,0.078] dBAcc[0.583,0.866] g[1.286,1.117] wind[0.149]
>34867, dALoss[0.021,0.010] dAAcc[0.990,1.000] dBLoss[0.070,0.030] dBAcc[1.000,0.970] g[1.165,1.892] wind[0.153]
>34868, dALoss[0.005,0.009] dAAcc[1.000,1.000] dBLoss[0.106,0.049] dBAcc[0.699,0.954] g[1.228,1.402] wind[0.173]
>34869, dALoss[0.019,0.006] dAAcc[1.000,1.000] dBLoss[0.043,0.086] dBAcc[0.972,0.778] g[0.781,1.

>34934, dALoss[0.005,0.005] dAAcc[1.000,1.000] dBLoss[0.017,0.081] dBAcc[1.000,0.783] g[1.349,1.847] wind[0.128]
>34935, dALoss[0.006,0.008] dAAcc[1.000,1.000] dBLoss[0.090,0.085] dBAcc[0.783,0.769] g[1.073,1.552] wind[0.173]
>34936, dALoss[0.022,0.026] dAAcc[0.997,0.987] dBLoss[0.087,0.029] dBAcc[0.762,0.990] g[1.373,1.224] wind[0.286]
>34937, dALoss[0.006,0.007] dAAcc[0.998,0.999] dBLoss[0.025,0.018] dBAcc[1.000,1.000] g[1.776,1.527] wind[0.341]
>34938, dALoss[0.012,0.004] dAAcc[0.998,1.000] dBLoss[0.037,0.066] dBAcc[0.966,0.844] g[1.092,1.926] wind[0.174]
>34939, dALoss[0.007,0.004] dAAcc[1.000,1.000] dBLoss[0.022,0.023] dBAcc[0.983,0.976] g[1.494,1.302] wind[0.194]
>34940, dALoss[0.001,0.005] dAAcc[1.000,1.000] dBLoss[0.011,0.029] dBAcc[0.990,0.999] g[2.284,2.066] wind[0.206]
>34941, dALoss[0.006,0.006] dAAcc[1.000,1.000] dBLoss[0.113,0.026] dBAcc[0.633,0.966] g[1.735,1.672] wind[0.214]
>34942, dALoss[0.004,0.006] dAAcc[1.000,1.000] dBLoss[0.032,0.032] dBAcc[0.998,0.954] g[1.659,2.

>35007, dALoss[0.004,0.004] dAAcc[1.000,1.000] dBLoss[0.076,0.027] dBAcc[0.843,0.967] g[1.436,1.490] wind[0.356]
>35008, dALoss[0.007,0.008] dAAcc[1.000,0.999] dBLoss[0.013,0.087] dBAcc[0.991,0.787] g[1.104,1.693] wind[0.288]
>35009, dALoss[0.005,0.009] dAAcc[1.000,1.000] dBLoss[0.041,0.026] dBAcc[0.989,0.996] g[1.395,1.914] wind[0.127]
>35010, dALoss[0.006,0.008] dAAcc[1.000,0.999] dBLoss[0.098,0.019] dBAcc[0.752,0.995] g[2.035,1.638] wind[0.127]
>35011, dALoss[0.004,0.006] dAAcc[1.000,1.000] dBLoss[0.090,0.034] dBAcc[0.737,0.961] g[1.556,1.595] wind[0.225]
>35012, dALoss[0.004,0.008] dAAcc[0.998,0.997] dBLoss[0.028,0.096] dBAcc[0.954,0.712] g[0.951,1.504] wind[0.230]
>35013, dALoss[0.005,0.046] dAAcc[0.993,0.973] dBLoss[0.072,0.052] dBAcc[0.823,0.899] g[1.058,1.191] wind[0.324]
>35014, dALoss[0.126,0.036] dAAcc[0.638,0.995] dBLoss[0.029,0.097] dBAcc[0.973,0.689] g[1.309,1.631] wind[0.142]
>35015, dALoss[0.016,0.006] dAAcc[1.000,0.999] dBLoss[0.013,0.016] dBAcc[0.992,1.000] g[1.794,1.

>35080, dALoss[0.004,0.005] dAAcc[0.999,1.000] dBLoss[0.065,0.037] dBAcc[0.918,0.971] g[1.388,1.653] wind[0.382]
>35081, dALoss[0.004,0.009] dAAcc[1.000,1.000] dBLoss[0.116,0.046] dBAcc[0.663,0.902] g[1.419,1.805] wind[0.197]
>35082, dALoss[0.005,0.023] dAAcc[1.000,0.995] dBLoss[0.012,0.034] dBAcc[0.990,0.988] g[1.313,1.725] wind[0.322]
>35083, dALoss[0.003,0.015] dAAcc[1.000,1.000] dBLoss[0.011,0.036] dBAcc[1.000,0.975] g[1.428,2.196] wind[0.113]
>35084, dALoss[0.004,0.010] dAAcc[0.999,0.992] dBLoss[0.043,0.017] dBAcc[0.952,0.979] g[1.666,1.569] wind[0.125]
>35085, dALoss[0.011,0.004] dAAcc[0.996,0.999] dBLoss[0.018,0.031] dBAcc[0.977,0.973] g[1.575,1.924] wind[0.264]
>35086, dALoss[0.012,0.022] dAAcc[0.994,0.985] dBLoss[0.019,0.146] dBAcc[0.977,0.538] g[0.459,1.230] wind[0.144]
>35087, dALoss[0.009,0.008] dAAcc[0.997,0.998] dBLoss[0.031,0.015] dBAcc[0.963,0.998] g[2.229,1.991] wind[0.150]
>35088, dALoss[0.004,0.005] dAAcc[1.000,1.000] dBLoss[0.021,0.043] dBAcc[0.996,0.991] g[1.658,1.